# Cleaning Robot
#### Lourdes Badillo, A01024232

Dado:

- Habitación de MxN espacios.
- Número de agentes.
- Porcentaje de celdas inicialmente sucias.
- Tiempo máximo de ejecución.

Realiza la siguiente simulación:

- Inicializa las celdas sucias (ubicaciones aleatorias).
- Todos los agentes empiezan en la celda [1,1].
- En cada paso de tiempo:
    - Si la celda está sucia, entonces aspira.
    - Si la celda está limpia, el agente elije una dirección aleatoria para moverse (unas de las 8 celdas vecinas) y elije la acción de movimiento (si no puede moverse allí, permanecerá en la misma celda).
- Se ejecuta el tiempo máximo establecido.

Deberás recopilar la siguiente información durante la ejecución:

- Tiempo necesario hasta que todas las celdas estén limpias (o se haya llegado al tiempo máximo).
- Porcentaje de celdas limpias después del termino de la simulación.
- Número de movimientos realizados por todos los agentes.


## Installations

In [ ]:
!pip install mesa

## Libraries

In [ ]:
from mesa import Agent, Model
from mesa.space import MultiGrid
from mesa.time import SimultaneousActivation
from mesa.datacollection import DataCollector
import numpy as np
import pandas as pd

#Animation Libraries
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as animation
plt.rcParams["animation.html"] = "jshtml"
matplotlib.rcParams['animation.embed_limit'] = 2**128

#Other libraries
import numpy as np
import pandas as pd
import random
import time
import datetime

## Classes

In [ ]:
def get_grid(model):
    """We need to generate the room which is a MxN grid"""
    grid = np.zeros((model.grid.width, model.grid.height))
    for (content, x, y) in model.grid.coord_iter():
        for data_content in content: 
            if isinstance(data_content, CleaningAgent):
                grid[x][y] = 2 #to differentiate in animation, it will be the darkest color
            else:
                grid[x][y] = data_content.state
    return grid


class Cell(Agent):
    """ Agent in each cell. The possible states are: clean or dirty""" 
    clean = 0
    dirty = 1
    def __init__(self, pos, model, state = clean):
        super().__init__(pos, model)
        self.x, self.y = pos
        self.state = state


class CleaningAgent(Agent):
    """ Agent representing the cleaning machines
        If a cell is dirty, it cleans it. 
        Move to any of its neighboring cells"""

    def __init__(self, unique_id, model):
        super().__init__(unique_id, model)
        self.nextPos = None
        self.moves = 0
    
    def step(self):
        # The agent's step will go here.
        neighbors = self.model.grid.get_neighbors(
            self.pos,
            moore = True, #we want the diagonals too
            include_center = True)
        
        for neighbor in neighbors: 
            if neighbor.pos == self.pos: 
                if neighbor.state == neighbor.dirty:
                    neighbor.state = neighbor.clean #clean it
                    self.nextPos = self.pos #move
                else:
                    possible_steps = self.model.grid.get_neighborhood(
                        self.pos, 
                        moore = True, 
                        include_center = False)
                    nextPos = self.random.choice(possible_steps)
                    self.nextPos = nextPos
                break

        if self.pos != self.nextPos: 
            self.moves += 1

        self.model.grid.move_agent(self, self.nextPos)

class CleaningModel(Model):
    """A model with some number of agents."""

    def __init__(self, M, N, total_agents, dirty_cells):
        self.total_agents = total_agents
        self.dirty_cells = dirty_cells
        self.clean_cells = 1-dirty_cells
        self.grid = MultiGrid(M,N, False) 
        self.schedule = SimultaneousActivation(self)

        #List of all cells
        cells = list(self.grid.empties)

        # Create agents
        for i in range(int((M*N)*dirty_cells)):
            rand_cell = random.choice(cells)
            cell = Cell(rand_cell, self)
            cell.state = cell.dirty
            self.grid.place_agent(cell, rand_cell)
            self.schedule.add(cell)
            cells.remove(rand_cell)
        
        #Empty cells are the clean ones
        clean_cells = list(self.grid.empties)
        for cells in clean_cells: 
            cell = Cell(cells, self)
            self.grid.place_agent(cell, cells)
            self.schedule.add(cell)
        
        # Add cleaning agents
        for i in range(total_agents):
            cleaner = CleaningAgent(i, self)
            self.grid.place_agent(cleaner, (1,1))
            self.schedule.add(cleaner)

        self.data_collector = DataCollector(
           model_reporters={'Grid': get_grid},
           agent_reporters={'Moves': lambda a: getattr(a, 'moves', None)} 
        )

    def step(self):
        self.data_collector.collect(self)
        self.schedule.step()

    def cleanRoom(self):
        cleaned = 0
        for cell in self.grid.coord_iter():
            cellContent, x, y = cell
            for content in cellContent:
                if isinstance(content, Cell) and content.state == content.clean:
                    cleaned += 1

        self.clean_cells = cleaned / (self.grid.width * self.grid.height)
        if self.clean_cells == 1: 
            return True
        else:
            return False
        

### Simulation 1

In [ ]:
M = 10
N = 12
total_agents = 2
dirty_cells = 0.5
max_time = 3
start_timer = time.time()
model = CleaningModel(M, N, total_agents, dirty_cells)

while((time.time()-start_timer)< max_time and not model.cleanRoom()):
    model.step()

execution_time = str(datetime.timedelta(seconds=(time.time() - start_timer)))



In [ ]:
all_grid = model.data_collector.get_model_vars_dataframe()

In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap='BuPu')

def animate(i):
    patch.set_data(all_grid.iloc[i][0])

anim = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
print('Cleaning Agents Simulation')
print('Room Size: ', M, ' x ', N)
print('Amount of cleaning agents: ', total_agents)
print('Dirty cells %: ', dirty_cells*100, '%')
print('Max time (s): ', max_time)
print('Cleaning time (s): ', execution_time)
print('Cleaned cells: ', model.clean_cells*100, '%')

moves = model.data_collector.get_agent_vars_dataframe()
print('Number of movements', moves.tail()['Moves'].sum())
anim

Cleaning Agents Simulation
Room Size:  10  x  12
Amount of cleaning agents:  2
Dirty cells %:  50.0 %
Max time (s):  3
Cleaning time (s):  0:00:00.349929
Cleaned cells:  100.0 %
Number of movements 1461.0


### Simulation 2

In [ ]:
M = 10
N = 12
total_agents = 4
dirty_cells = 0.5
max_time = 3
start_timer = time.time()
model = CleaningModel(M, N, total_agents, dirty_cells)

while((time.time()-start_timer)< max_time and not model.cleanRoom()):
    model.step()

execution_time = str(datetime.timedelta(seconds=(time.time() - start_timer)))

all_grid = model.data_collector.get_model_vars_dataframe()

In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap='BuPu')

def animate(i):
    patch.set_data(all_grid.iloc[i][0])

anim2 = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
print('Cleaning Agents Simulation')
print('Room Size: ', M, ' x ', N)
print('Amount of cleaning agents: ', total_agents)
print('Dirty cells %: ', dirty_cells*100, '%')
print('Max time (s): ', max_time)
print('Cleaning time (s): ', execution_time)
print('Cleaned cells: ', model.clean_cells*100, '%')

moves = model.data_collector.get_agent_vars_dataframe()
print('Number of movements', moves.tail()['Moves'].sum())
anim2

Cleaning Agents Simulation
Room Size:  10  x  12
Amount of cleaning agents:  4
Dirty cells %:  50.0 %
Max time (s):  3
Cleaning time (s):  0:00:00.097662
Cleaned cells:  100.0 %
Number of movements 721.0


### Simulation 3

In [ ]:
M = 10
N = 12
total_agents = 8
dirty_cells = 0.5
max_time = 3
start_timer = time.time()
model = CleaningModel(M, N, total_agents, dirty_cells)

while((time.time()-start_timer)< max_time and not model.cleanRoom()):
    model.step()

execution_time = str(datetime.timedelta(seconds=(time.time() - start_timer)))
all_grid = model.data_collector.get_model_vars_dataframe()

In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap='BuPu')

def animate(i):
    patch.set_data(all_grid.iloc[i][0])

anim3 = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
print('Cleaning Agents Simulation')
print('Room Size: ', M, ' x ', N)
print('Amount of cleaning agents: ', total_agents)
print('Dirty cells: ', dirty_cells*100, '%')
print('Max time (s): ', max_time)
print('Cleaning time (s): ', execution_time)
print('Cleaned cells: ', model.clean_cells*100, '%')

moves = model.data_collector.get_agent_vars_dataframe()
print('Number of movements', moves.tail()['Moves'].sum())
anim3

Cleaning Agents Simulation
Room Size:  10  x  12
Amount of cleaning agents:  8
Dirty cells:  50.0 %
Max time (s):  3
Cleaning time (s):  0:00:00.097096
Cleaned cells:  100.0 %
Number of movements 728.0


### Simulation 4

In [ ]:
M = 10
N = 12
total_agents = 16
dirty_cells = 0.5
max_time = 3
start_timer = time.time()
model = CleaningModel(M, N, total_agents, dirty_cells)

while((time.time()-start_timer)< max_time and not model.cleanRoom()):
    model.step()

execution_time = str(datetime.timedelta(seconds=(time.time() - start_timer)))
all_grid = model.data_collector.get_model_vars_dataframe()

In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap='BuPu')

def animate(i):
    patch.set_data(all_grid.iloc[i][0])

anim4 = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
print('Cleaning Agents Simulation')
print('Room Size: ', M, ' x ', N)
print('Amount of cleaning agents: ', total_agents)
print('Dirty cells: ', dirty_cells*100, '%')
print('Max time (s): ', max_time)
print('Cleaning time (s): ', execution_time)
print('Cleaned cells: ', model.clean_cells*100, '%')

moves = model.data_collector.get_agent_vars_dataframe()
print('Number of movements', moves.tail()['Moves'].sum())
anim4

Cleaning Agents Simulation
Room Size:  10  x  12
Amount of cleaning agents:  16
Dirty cells:  50.0 %
Max time (s):  3
Cleaning time (s):  0:00:00.076535
Cleaned cells:  100.0 %
Number of movements 479.0


### Simulation 5

In [ ]:
M = 10
N = 12
total_agents = 32
dirty_cells = 0.5
max_time = 3
start_timer = time.time()
model = CleaningModel(M, N, total_agents, dirty_cells)

while((time.time()-start_timer)< max_time and not model.cleanRoom()):
    model.step()

execution_time = str(datetime.timedelta(seconds=(time.time() - start_timer)))
all_grid = model.data_collector.get_model_vars_dataframe()

In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap='BuPu')

def animate(i):
    patch.set_data(all_grid.iloc[i][0])

anim5 = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
print('Cleaning Agents Simulation')
print('Room Size: ', M, ' x ', N)
print('Amount of cleaning agents: ', total_agents)
print('Dirty cells: ', dirty_cells*100, '%')
print('Max time (s): ', max_time)
print('Cleaning time (s): ', execution_time)
print('Cleaned cells: ', model.clean_cells*100, '%')

moves = model.data_collector.get_agent_vars_dataframe()
print('Number of movements', moves.tail()['Moves'].sum())
anim5

Cleaning Agents Simulation
Room Size:  10  x  12
Amount of cleaning agents:  32
Dirty cells:  50.0 %
Max time (s):  3
Cleaning time (s):  0:00:00.079921
Cleaned cells:  100.0 %
Number of movements 250.0


### Simulation 6

In [ ]:
M = 10
N = 12
total_agents = 64
dirty_cells = 0.5
max_time = 3
start_timer = time.time()
model = CleaningModel(M, N, total_agents, dirty_cells)

while((time.time()-start_timer)< max_time and not model.cleanRoom()):
    model.step()

execution_time = str(datetime.timedelta(seconds=(time.time() - start_timer)))
all_grid = model.data_collector.get_model_vars_dataframe()

In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap='BuPu')

def animate(i):
    patch.set_data(all_grid.iloc[i][0])

anim6 = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
print('Cleaning Agents Simulation')
print('Room Size: ', M, ' x ', N)
print('Amount of cleaning agents: ', total_agents)
print('Dirty cells: ', dirty_cells*100, '%')
print('Max time (s): ', max_time)
print('Cleaning time (s): ', execution_time)
print('Cleaned cells: ', model.clean_cells*100, '%')

moves = model.data_collector.get_agent_vars_dataframe()
print('Number of movements', moves.tail()['Moves'].sum())
anim6

Cleaning Agents Simulation
Room Size:  10  x  12
Amount of cleaning agents:  64
Dirty cells:  50.0 %
Max time (s):  3
Cleaning time (s):  0:00:00.071385
Cleaned cells:  100.0 %
Number of movements 187.0
